### OSMGetPOI.jl Tutorial
Full documentation: https://github.com/mkloe/OSMgetPOI

In [1]:
using OSMgetPOI

### 1. Download .osm data file
- Downloading from Geofabrik
    1. Go to https://download.bbbike.org/osm/bbbike/ and select a city.
    2. Copy URL of *OSM XML gzip'd* file (exemplary URL: https://download.bbbike.org/osm/bbbike/Corsica/Corsica.osm.gz)
- Downloading from BBBike
    1. Go to https://download.geofabrik.de/index.html and select a city or region.
    2. Get URL of *.osm.bz2* file (examplary URL: https://download.geofabrik.de/asia/maldives-latest.osm.bz2)


Downloading file from BBBike

In [14]:
download_bbbike_file("https://download.bbbike.org/osm/bbbike/Singapore/Singapore.osm.gz")

File downloaded. Unzipping file...
File saved at 

datasets/file.osm

Downloading file from Geofabrik

In [7]:
download_geofabrik_file("https://download.geofabrik.de/asia/bhutan-latest.osm.bz2")

File downloaded. Unzipping file...
File saved at 

datasets/file.osm

### 2. Generate a dataframe 
Generate a dataframe with the POI types defined in the parameters, based on `src/POITypes`. More information about the supported POI types by this API is provided in the documentation.

In [30]:
schools = get_poi_df("datasets/file.osm", 1.0, ["addr:housenumber", "addr:street", "addr:postcode", "addr:country"], OSMgetPOI.POITypes.education_school, OSMgetPOI.POITypes.transport_busstop, OSMgetPOI.POITypes.cuisine_restaurant)

OSM filter process time: 2.304034708


OSM filter process time: 2.209437792


OSM filter process time: 2.213192041


6802×7 DataFrame
  Row │ poi_type            lat      lon      addr:housenumber  addr:country   ⋯
      │ Any                 Any      Any      Any               Any            ⋯
──────┼─────────────────────────────────────────────────────────────────────────
    1 │ education_school    1.31934  103.745  698               SG             ⋯
    2 │ education_school    1.34098  103.952  11                SG
    3 │ education_school    1.2885   103.809  missing           missing       
    4 │ education_school    1.28493  103.829  missing           missing      
    5 │ education_school    1.35807  103.863  2C                SG             ⋯
    6 │ education_school    1.47666  103.745  missing           missing      
    7 │ education_school    1.39324  103.876  15                SG
    8 │ education_school    1.34786  103.718  missing           missing       
  ⋮   │         ⋮              ⋮        ⋮            ⋮               ⋮         ⋱
 6796 │ cuisine_restaurant  1.45655  103.764  missing           missing        ⋯
 6797 │ cuisine_restaurant  1.31224  103.923  missing           missing      
 6798 │ cuisine_restaurant  1.32122  103.887  missing           missing       
 6799 │ cuisine_restaurant  1.27906  103.845  missing           missing      
 6800 │ cuisine_restaurant  1.2802   103.847  198               SG             ⋯
 6801 │ cuisine_restaurant  1.30148  103.836  missing           missing       
 6802 │ cuisine_restaurant  1.30275  103.852  missing           missing       
                                                 2 columns and 6787 rows omitted

### 3. Save the results to a .csv file.

In [10]:
using CSV
CSV.write("output_csv/schools.csv", schools)

"output_csv/schools.csv"

### 4. Visualising POIs on the map

In [3]:
using PyCall
folium = pyimport("folium")
colors = ["red", "blue", "gray", "darkred", "lightred", "orange", "beige", "green", "darkgreen", 
    "lightgreen", "darkblue", "lightblue", "purple", "darkpurple", "pink", "cadetblue", "lightgray", "black"]

PyObject <module 'folium' from '/Users/marcinzurek/.julia/conda/3/lib/python3.9/site-packages/folium/__init__.py'>

In [31]:
m = folium.Map(location = [schools.lat[1], schools.lon[1]], zoom_start=11)

for i in 1:size(schools,1)
    poi_types = unique(schools.poi_type)
    street = schools[i,"addr:street"]
    number = schools[i, "addr:housenumber"]
    postcode = schools[i, "addr:postcode"]
    poi_color = colors[((findall(x -> x==schools[i,"poi_type"], poi_types)[1]-1) % length(colors)) + 1]
    poi_type = schools[i,"poi_type"]
    folium.Circle(
        location = (schools.lat[i], schools.lon[i]),
        radius = 100,
        tooltip = "<b>POI: </b>$poi_type<br><br><b>Address</b><br>Street: $street<br>Number: $number<br>Postcode: $postcode",
        color = poi_color,
        fill = false,
        fill_color = poi_color
    ).add_to(m)
end
m

PyObject <folium.folium.Map object at 0x173b4ea60>

### Remarks
This research was funded in whole or in part by [National Science Centre,  Poland][2021/41/B/HS4/03349]. For the software’s  documentation for the purpose of Open Access, the author has applied a CC-BY public copyright licence to any Author Accepted Manuscript (AAM) version arising from this submission.